## Config and Module

In [1]:
ADAPTER_CONFIG = {
    "adapter_id": "003",
    "name": "DualShuntAdapter-G",

    "t5": {
        "model": "google/flan-t5-base",
        "hidden_size": 768,
    },
    "clip": {
        "model": "AbstractPhil/omega-vit-g-reformed",
        "hidden_size": 1280,
    },

    "bottleneck": 640,
    "heads": 20,

    "tau_init": 0.1,
    "max_guidance": 10.0,

    "proj_layers": 2,
    "layer_norm": True,
    "dropout": 0.1,
    "use_dropout": True,
    "use_proj_stack": True,
    "assert_input_dims": True,

    "routing": {
        "type": "cross_attention",
        "enable_causal_mask": False,
        "bidirectional": True
    },

    "version": "v0.3.2",
    "description": "Final Dual Shunt Adapter with projection stack, dropout, and stacked residual refinement pocket."
}


In [2]:
import torch
import torch.nn as nn
import torch.nn.functional as F

# ─── Residual Pocket Block ───────────────────────────────────
class BottleneckResBlock(nn.Module):
    def __init__(self, dim, kernel=3, dropout=0.1):
        super().__init__()
        self.norm = nn.LayerNorm(dim)
        self.conv = nn.Conv1d(dim, dim, kernel_size=kernel, padding=kernel // 2, groups=1)
        self.proj = nn.Sequential(
            nn.Linear(dim, dim * 2),
            nn.GELU(),
            nn.Linear(dim * 2, dim),
            nn.Dropout(dropout)
        )

    def forward(self, x):
        residual = x
        x = self.norm(x)
        x = x.transpose(1, 2)
        x = self.conv(x).transpose(1, 2)
        return residual + self.proj(x)

# ─── Two Stream Shunt Adapter ──────────────────────────────────────
class TwoStreamShuntAdapter(nn.Module):
    def __init__(self, config: dict):
        super().__init__()
        self.config = config
        self.t5_dim = config["t5"]["hidden_size"]
        self.clip_dim = config["clip"]["hidden_size"]
        self.bneck = config["bottleneck"]
        self.heads = config["heads"]
        self.tau_init = config["tau_init"]
        self.max_guidance = config["max_guidance"]

        use_norm   = config.get("layer_norm", True)
        use_do     = config.get("use_dropout", True)
        do_p       = config.get("dropout", 0.1)
        proj_depth = config.get("proj_layers", 2)

        def build_projection(input_dim, output_dim):
            layers = []
            last_dim = input_dim
            if use_norm:
                layers.append(nn.LayerNorm(last_dim))
            for i in range(proj_depth):
                next_dim = self.bneck * (2 if i == 0 and proj_depth > 1 else 1)
                layers.append(nn.Linear(last_dim, next_dim))
                layers.append(nn.GELU())
                if use_do:
                    layers.append(nn.Dropout(do_p))
                last_dim = next_dim
            layers.append(nn.Linear(last_dim, output_dim))
            return nn.Sequential(*layers)

        # Projections
        self.proj_t5   = build_projection(self.t5_dim, self.bneck)
        self.proj_clip = build_projection(self.clip_dim, self.bneck)

        # Attention
        self.cross_t2c = nn.MultiheadAttention(self.bneck, self.heads, batch_first=True, dropout=do_p)
        self.cross_c2t = nn.MultiheadAttention(self.bneck, self.heads, batch_first=True, dropout=do_p)
        self.tau       = nn.Parameter(torch.full((self.heads, 1, 1), self.tau_init))

        # Residual Pocket
        self.pocket_blocks = nn.Sequential(
            BottleneckResBlock(self.bneck, dropout=do_p),
            BottleneckResBlock(self.bneck, dropout=do_p)
        )

        # Fuse
        self.fuse = nn.Sequential(
            nn.LayerNorm(2 * self.bneck),
            nn.Linear(2 * self.bneck, self.bneck * 2),
            nn.GELU(),
            nn.Linear(self.bneck * 2, self.bneck)
        )

        # Output Projections
        self.anchor_proj = build_projection(self.bneck, self.clip_dim)
        self.delta_proj  = build_projection(self.bneck, self.clip_dim)
        self.logsig_proj = build_projection(self.bneck, self.clip_dim)

        self.gate_proj = nn.Sequential(
            nn.LayerNorm(self.bneck),
            nn.Linear(self.bneck, self.bneck),
            nn.GELU(),
            nn.Linear(self.bneck, 1),
            nn.Tanh(),
            nn.Sigmoid()
        )

        self.guidance_proj = nn.Sequential(
            nn.LayerNorm(self.bneck),
            nn.Linear(self.bneck, 1),
            nn.Sigmoid()
        )

    def forward(self, t5_seq: torch.Tensor, clip_seq: torch.Tensor):
        if self.config.get("assert_input_dims", True):
            assert t5_seq.size(-1) == self.t5_dim
            assert clip_seq.size(-1) == self.clip_dim

        t5_b   = self.proj_t5(t5_seq)
        clip_b = self.proj_clip(clip_seq)

        t2c, attn_t2c = self.cross_t2c(t5_b, clip_b, clip_b, need_weights=True, average_attn_weights=False)
        c2t, attn_c2t = self.cross_c2t(clip_b, t5_b, t5_b, need_weights=True, average_attn_weights=False)

        pocket = self.pocket_blocks(t2c)

        pocket_mean = pocket.mean(1, keepdim=True).expand(-1, clip_b.size(1), -1)
        h = self.fuse(torch.cat([pocket_mean, c2t], dim=-1))

        anchor    = self.anchor_proj(h)
        delta     = self.delta_proj(h) * self.gate_proj(h)
        log_sigma = self.logsig_proj(h)

        g_tok  = self.guidance_proj(h).squeeze(-1)
        g_pred = g_tok.mean(1, keepdim=True) * self.max_guidance

        return anchor, delta, log_sigma, attn_t2c, attn_c2t, self.tau, g_pred, self.gate_proj(h)


In [3]:
from safetensors.torch import save_file, load_file

def save_safetensors(adapter: nn.Module, path: str, metadata: dict = None):
    """
    Save the current adapter state to safetensors format.

    All tensors are moved to CPU and saved as float32 for compatibility.
    Optional metadata may be embedded (e.g., version, prompt_mode).
    """
    state = {k: v.float().cpu() for k, v in adapter.state_dict().items()}
    save_file(state, path, metadata=metadata or {})
    print(f"✅ Model saved to {path}")

def load_safetensors(adapter: nn.Module, path: str, map_location="cpu"):
    """
    Load a safetensors checkpoint into the adapter.

    Uses strict key matching. Tensors are loaded to the specified device.
    """
    state = load_file(path, device=map_location)
    adapter.load_state_dict(state, strict=True)
    print(f"✅ Model loaded from {path}")




## Data Loader

In [4]:
import torch
import csv

# ─────────────────────────────────────────────────────────────
# ░ Streaming Caption Dataset
# ─────────────────────────────────────────────────────────────
# ─────────────────────────────────────────────────────────────
# ░ Streaming Caption Dataset – 32 quality descriptors
# ─────────────────────────────────────────────────────────────
import csv, random, re
from typing import List
from torch.utils.data import IterableDataset, get_worker_info
from huggingface_hub import hf_hub_download
from torch.utils.data import DataLoader
from pathlib import Path


class ParsedMultiCharDataset(IterableDataset):
    """
    Streams HF-hosted caption shards and, for each text chunk:

      • If it starts with “a ” (case-insensitive, ignoring leading spaces),
        replace that leading token with a random photo/video quality
        descriptor followed by “, ”.

    No preliminary file scanning; every CSV line is read exactly once.
    """

    # match leading “a ” only
    _PAT_START_A = re.compile(r"^\s*a\s+", re.IGNORECASE)

    # 32 diverse quality descriptors
    _QUALITY_DESCRIPTORS: List[str] = [
        "masterpiece,",
        "very aesthetic,",
        "most aesthetic,",
        "an absolutely perfect depiction of",
        "awa,",
        "very awa,",
        "dimly lit,",
        "beautifuly lit,",
        "very beautiful,",
        "masterful depiction of",
        "dedicated masterpiece,",
        "warmly lit",
        "best quality, most aesthetic,",
        "beautiful depiction of",
        "masterful artwork of",
        "high-resolution photograph,",
        "hyper-realistic image,",
        "ultra-detailed photo,",
        "studio-quality photograph,",
        "cinematic shot,",
        "4K HDR image,",
        "sharp-focus photo,",
        "professionally lit photograph,",
        "DSLR capture,",
        "film-grain photograph,",
        "bokeh-rich shot,",
        "medium-format scan,",
        "analog film still,",
        "moody cinematic frame,",
        "dramatic-lighting photo,",
        "vibrant editorial image,",
        "macro-lens close-up,",
        "aerial drone photo,",
        "soft-focus dreamlike photo,",
        "low-key studio shot,",
        "overhead product shot,",
        "golden-hour photograph,",
        "noir-style monochrome shot,",
        "vintage Polaroid scan,",
        "infrared photograph,",
        "ultra-wide panorama,",
        "tilt-shift miniature photo,",
        "long-exposure night shot,",
        "time-lapse still,",
        "splash-photography frame,",
        "fine-art print scan,",
        "astrophotography capture,",
        "score_9, score_8, score_7, score_6,",
        "score_1, score_2, score_3, score_4,",
        "masterpiece, most aesthetic,",
        "most aesthetic, very aesthetic,",
        "masterpiece, most aesthetic, very aesthetic, realistic, real,",
        "most aesthetic, realistic, real,",
        "very aesthetic, realistic, real,",
        "masterpiece, very aesthetic, realistic, real,",
        "most aesthetic, very aesthetic, realistic, real,",
        "masterpiece, very aesthetic, realistic, anime,",
        "most aesthetic, very aesthetic, realistic, anime,",
        "very aesthetic, realistic, anime,",
        "masterpiece, very aesthetic, realistic, anime,",
        "most aesthetic, very aesthetic, realistic, anime,",
        "very aesthetic, realistic, anime, anime,",
        "2d,",
        "3d,",
        "anime,",
        "real,",
        "cartoon,"
        "realistic,",
        "2d,",
        "3d,",
        "anime,",
        "real,",
        "cartoon,"
        "realistic,",
        "2d,",
        "3d,",
        "anime,",
        "real,",
        "cartoon,"
        "realistic,",
        "2d,",
        "3d,",
        "anime,",
        "real,",
        "cartoon,"
        "realistic,",
        "masterpiece, 2d,",
        "masterpiece, 3d,",
        "masterpiece, anime,",
        "masterpiece, real,",
        "masterpiece, cartoon,",
        "3d, anime,",
        "3d, anime, real,",
        "3d, anime, real, realistic,",
        "masterpiece, 3d,",
        "masterpiece, 3d, anime,",
        "masterpiece, 3d, anime, real,",
        "masterpiece, 3d, anime, real, realistic,",
        "masterpiece, anime,",
        "masterpiece, anime, real,",
        "masterpiece, anime, real, realistic,",
        "masterpiece, 3d, anime, real,",
        "very aesthetic, 3d,",
        "very aesthetic, 3d, anime,",
        "very aesthetic, 3d, anime, real,",
        "very aesthetic, 3d, anime, real, realistic,",
        "very aesthetic, 3d, anime, real,",
        "most aesthetic, 3d,",
        "most aesthetic, 3d, anime,",
        "most aesthetic, 3d, anime, real,",
        "most aesthetic, 3d, anime, real, realistic,",
        "anime, comic,"
        "manga, anime",
        "masterpiece, cartoon,",
        "masterpiece, cartoon, real,",
        "masterpiece, cartoon, real, realistic,",
        "masterpiece, cartoon, real,",
        "most aesthetic, cartoon,",
        "most aesthetic, cartoon, real,",
        "most aesthetic, cartoon, real, realistic,",
        "most aesthetic, cartoon, real,",
        "grid_a1 head,"
        "grid_a2 head,",
        "grid_a3 head,",
        "grid_a4 head,",
        "grid_a5 head,",
        "grid_b1 head,"
        "grid_b2 head,",
        "grid_b3 head,",
        "grid_b4 head,",
        "grid_b5 head,",
        "grid_c1 head,"
        "grid_c2 head,",
        "grid_c3 head,",
        "grid_c4 head,",
        "grid_c5 head,",
        "grid_d1 head,"
        "grid_d2 head,",
        "grid_d3 head,",
        "grid_d4 head,",
        "grid_d5 head,",
        "grid_e1 head,"
        "grid_e2 head,",
        "grid_e3 head,",
        "grid_e4 head,",
        "grid_e5 head,",
        "grid_a1 upper body,"
        "grid_a2 upper body,",
        "grid_a3 upper body,",
        "grid_a4 upper body,",
        "grid_a5 upper body,",
        "grid_b1 upper body,"
        "grid_b2 upper body,",
        "grid_b3 upper body,",
        "grid_b4 upper body,",
        "grid_b5 upper body,",
        "grid_c1 upper body,"
        "grid_c2 upper body,",
        "grid_c3 upper body,",
        "grid_c4 upper body,",
        "grid_c5 upper body,",
        "grid_d1 upper body,"
        "grid_d2 upper body,",
        "grid_d3 upper body,",
        "grid_d4 upper body,",
        "grid_d5 upper body,",
        "grid_e1 upper body,"
        "grid_e2 upper body,",
        "grid_e3 upper body,",
        "grid_e4 upper body,",
        "grid_e5 upper body,",
        "zone_ul upper body,"
        "zone_ur upper body,"
        "zone_ll upper body,"
        "zone_lr upper body,",
        "zone_ul head,"
        "zone_ur head,"
        "zone_ll head,"
        "zone_lr head,",

        #"disgusting, 3d, lowres,",
        #"disgusting, 2d, lowres,",
        #"disgusting, cartoon, lowres,",
        #"disgusting, 3d, cartoon, lowres,",
        #"disgusting, 2d, cartoon, lowres,",
        #"disgusting


    ]

    def __init__(
        self,
        repo_id: str,
        delimiter: str = ".,|,.",
        start_file: int = 20,
        num_files: int = 80,
        shuffle: bool = False
    ):
        super().__init__()
        self.delimiter = delimiter
        self.paths = [
            hf_hub_download(
                repo_id,
                f"captions/caption_{i + start_file:03d}.csv",
                repo_type="dataset",
            )
            for i in range(num_files)
        ]
        self.total_rows = 5_000_000 * num_files
        self.shuffle = shuffle

    def __len__(self):
        return self.total_rows

    def __iter__(self):
        worker = get_worker_info()
        paths = (
            self.paths
            if worker is None
            else self.paths[worker.id :: worker.num_workers]
        )

        pat_a   = self._PAT_START_A
        choose  = random.choice
        q_pool  = self._QUALITY_DESCRIPTORS
        delim   = self.delimiter

        for path in paths:
            with open(path, encoding="utf-8", newline="") as f:
                for row in csv.DictReader(f):
                    for chunk in row.get("text", "").split(delim):
                        chunk = chunk.strip()
                        if not chunk:
                            continue
                        if self.shuffle:
                            random.shuffle(q_pool)
                        # replace leading “a ” with descriptor + comma
                        chunk = pat_a.sub(choose(q_pool) + " ", chunk, count=1)

                        yield chunk




## Load Models

In [5]:
import torch
from transformers import (
    T5EncoderModel, T5TokenizerFast,
    CLIPTextModel, CLIPTokenizerFast
)

import torch
from transformers import (
    T5EncoderModel, T5TokenizerFast,
    CLIPTextModel, CLIPTokenizerFast
)

from safetensors.torch import save_file, load_file


# ─── Runtime Settings ────────────────────────────────────────
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")
DTYPE = torch.float32  # 🔒 Force full FP32 precision

# ─── Load Tokenizers ─────────────────────────────────────────
t5_tok = T5TokenizerFast.from_pretrained("google/flan-t5-base")
clip_tok = CLIPTokenizerFast.from_pretrained("laion/CLIP-ViT-bigG-14-laion2B-39B-b160k")

# ─── Load and Freeze T5 Model ───────────────────────────────
t5_mod = T5EncoderModel.from_pretrained("google/flan-t5-base").to(DEVICE, dtype=DTYPE)
t5_mod.eval().requires_grad_(False)

# ─── Load and Freeze CLIP Model ─────────────────────────────
clip_mod = CLIPTextModel.from_pretrained("laion/CLIP-ViT-bigG-14-laion2B-39B-b160k").to(DEVICE, dtype=DTYPE)


print(clip_mod.state_dict().keys())

temp_clip = load_file("/content/drive/MyDrive/clips/OMEGA-24-CLIP_G.safetensors")

print(temp_clip.keys())

clip_mod.load_state_dict(temp_clip, strict=False)
clip_mod.eval().requires_grad_(False)
## ─── Load Dual Shunt Adapter ────────────────────────────────
#adapter = DualShuntAdapter(config=ADAPTER_CONFIG).to(DEVICE, dtype=DTYPE)
#
#
#print("✅ All models loaded at float32 precision and ready.")

# ─── Initialize Adapter from Config ──────────────────────────
adapter = TwoStreamShuntAdapter(config=ADAPTER_CONFIG).to(DEVICE, dtype=DTYPE)
load_safetensors(adapter, "/content/drive/MyDrive/dual_shunt_runs_omega_g/dual_shunt_omega_no_caption_e1_step_10000.safetensors")
adapter.train()
print("✅ T5, CLIP, and Dual Shunt Adapter loaded and cast.")


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

odict_keys(['text_model.embeddings.token_embedding.weight', 'text_model.embeddings.position_embedding.weight', 'text_model.encoder.layers.0.self_attn.k_proj.weight', 'text_model.encoder.layers.0.self_attn.k_proj.bias', 'text_model.encoder.layers.0.self_attn.v_proj.weight', 'text_model.encoder.layers.0.self_attn.v_proj.bias', 'text_model.encoder.layers.0.self_attn.q_proj.weight', 'text_model.encoder.layers.0.self_attn.q_proj.bias', 'text_model.encoder.layers.0.self_attn.out_proj.weight', 'text_model.encoder.layers.0.self_attn.out_proj.bias', 'text_model.encoder.layers.0.layer_norm1.weight', 'text_model.encoder.layers.0.layer_norm1.bias', 'text_model.encoder.layers.0.mlp.fc1.weight', 'text_model.encoder.layers.0.mlp.fc1.bias', 'text_model.encoder.layers.0.mlp.fc2.weight', 'text_model.encoder.layers.0.mlp.fc2.bias', 'text_model.encoder.layers.0.layer_norm2.weight', 'text_model.encoder.layers.0.layer_norm2.bias', 'text_model.encoder.layers.1.self_attn.k_proj.weight', 'text_model.encoder.la

In [6]:

clip_mod.load_state_dict(temp_clip, strict=False)
clip_mod = torch.compile(clip_mod, mode="reduce-overhead", dtype=torch.float32)
## ─── Load Dual Shunt Adapter ────────────────────────────────

TypeError: compile() got an unexpected keyword argument 'dtype'

# Noise Train

In [13]:
import torch
import torch.nn.functional as F
from tqdm import tqdm
from pathlib import Path


def train_dual_shunt(
    t5_tok, clip_tok, t5_mod, clip_mod, adapter,
    repo_id: str,
    batch_size: int = 256,
    epochs: int = 1,
    lr: float = 5e-4,
    device: str = "cuda",
    g_target: float = 7.5,
    λ_delta: float = 1.0,
    λ_gate: float  = 0.15,
    λ_ent: float   = 0.02,
    λ_tau: float   = 0.02,
    λ_anchor: float= 0.12,
    λ_guid: float  = 0.1,
    save_every: int = 1000,
    max_token_length: int = 77,
    seed: int = 42,
    t5_prompt_mode: str = "real_raw",
    output_dir: str = "/content/drive/MyDrive/dual_shunt_runs_omega_g"
):
    import torch
    import torch.nn.functional as F
    from tqdm import tqdm
    from pathlib import Path
    import random

    def extract_sparse_tokens(text: str, keep_min: int = 1, keep_max: int = 5, keep_prob: float = 0.3) -> str:
        words = text.strip().split()
        keep_count = min(len(words), random.randint(keep_min, keep_max))
        indices = sorted(random.sample(range(len(words)), k=keep_count))
        return " ".join(words[i] for i in indices)

    def seed_everything(seed: int = 42):
        torch.manual_seed(seed)
        torch.cuda.manual_seed_all(seed)
        torch.backends.cudnn.deterministic = True
        torch.backends.cudnn.benchmark = False

    LOG_2PI = 1.83787706641

    def hetero_loss(delta, target, log_sigma):
        log_sigma = log_sigma.clamp(-5.0, 5.0)
        inv_var = torch.exp(-log_sigma)
        return 0.5 * (inv_var * (delta - target)**2 + log_sigma + LOG_2PI).mean()

    def entropy(p: torch.Tensor) -> torch.Tensor:
        p = p / (p.sum(-1, keepdim=True) + 1e-9)
        return -(p * (p + 1e-9).log()).sum(-1).mean()

    # ─── Setup ───────────────────────────────────────────────
    seed_everything(seed)
    device = torch.device(device)

    ds = ParsedMultiCharDataset(repo_id, start_file=50, num_files=6, shuffle=True)
    dl = torch.utils.data.DataLoader(
        ds, batch_size=batch_size, num_workers=4,
        drop_last=True, persistent_workers=True,
        generator=torch.Generator().manual_seed(seed),
        prefetch_factor=8
    )

    output_dir = Path(output_dir)
    output_dir.mkdir(parents=True, exist_ok=True)
    global_step = 0

    opt = torch.optim.AdamW(adapter.parameters(), lr=lr)
    scaler = torch.amp.GradScaler(device="cuda")

    # ─── Training Loop ───────────────────────────────────────
    for epoch in range(1, epochs + 1):
        pbar = tqdm(dl, desc=f"Epoch {epoch}/{epochs}")
        for texts in pbar:
            global_step += 1

            with torch.autocast(device.type, dtype=torch.bfloat16):
                # T5 prompt encoding
                t5_inputs = t5_tok(texts, padding=True, truncation=True,
                                   max_length=max_token_length, return_tensors="pt").to(device)
                with torch.no_grad():
                    t5_seq = t5_mod(**t5_inputs).last_hidden_state

                # CLIP (plain)
                clip_inputs = clip_tok(texts, padding="max_length", truncation=True,
                                       max_length=max_token_length, return_tensors="pt").to(device)
                with torch.no_grad():
                    clip_seq_plain = clip_mod(**clip_inputs).last_hidden_state

                # CLIP (captioned target)

                # for null noise training
                cap_texts = [f"{extract_sparse_tokens(t)}" for t in texts]
                clip_inputs_cap = clip_tok(cap_texts, padding="max_length", truncation=True,
                                           max_length=max_token_length, return_tensors="pt").to(device)
                with torch.no_grad():
                    clip_seq_cap = clip_mod(**clip_inputs_cap).last_hidden_state

                #with torch.no_grad():
                #    summary_ids = t5_mod.generate(**t5_inputs, max_length=max_token_length)
                #    cap_texts = t5_tok.batch_decode(summary_ids, skip_special_tokens=True)

                # Encode summaries into CLIP
                #clip_inputs_cap = clip_tok(cap_texts, padding="max_length", truncation=True,
                #                          max_length=max_token_length, return_tensors="pt").to(device)
                #with torch.no_grad():
                #    clip_seq_cap = clip_mod(**clip_inputs_cap).last_hidden_state

                # Adapter forward
                anchor, delta, log_sigma, attn_t2c, attn_c2t, tau, g_pred, gate = adapter(t5_seq, clip_seq_plain)
                delta_tgt = clip_seq_cap - clip_seq_plain

                # 🔧 SAFE attention projection for auxiliary losses
                with torch.no_grad():
                    t5_b   = adapter.proj_t5(t5_seq)
                    clip_b = adapter.proj_clip(clip_seq_plain)
                    t2c_base, _ = adapter.cross_t2c(t5_b, clip_b, clip_b)
                    c2t_base, _ = adapter.cross_c2t(clip_b, t5_b, t5_b)

                pocket = adapter.pocket_blocks(t2c_base.detach())
                loss_pocket = F.mse_loss(pocket, t2c_base.detach()) * 0.05

                fused_h = adapter.fuse(torch.cat([
                    pocket.mean(1, keepdim=True).expand(-1, clip_b.size(1), -1),
                    c2t_base
                ], dim=-1))
                loss_hidden = (fused_h.norm(dim=-1).mean() - 1.0).abs() * 0.01

                # Core losses
                loss_delta  = hetero_loss(delta, delta_tgt, log_sigma) * λ_delta
                loss_gate   = (gate.mean() - 0.25).abs() * λ_gate
                loss_ent    = 0.5 * (entropy(attn_t2c) + entropy(attn_c2t)) * λ_ent
                loss_tau    = tau.abs().mean() * λ_tau
                loss_anchor = (1 - F.cosine_similarity(anchor.mean(1), clip_seq_plain.mean(1), dim=-1).mean()) * λ_anchor
                loss_guid   = F.mse_loss(g_pred, torch.full_like(g_pred, g_target)) * λ_guid

                total_loss = (
                    loss_delta + loss_gate + loss_ent +
                    loss_tau + loss_anchor + loss_guid +
                    loss_pocket + loss_hidden
                )

            # Backprop + step
            scaler.scale(total_loss).backward()
            scaler.step(opt)
            scaler.update()
            opt.zero_grad(set_to_none=True)
            if global_step % 100 == 0:
                print(f"Gate mean: {gate.mean().item():.3f}  log_sigma mean: {log_sigma.mean().item():.3f}")
            if global_step % save_every == 0:
                path = output_dir / f"dual_shunt_omega_{t5_prompt_mode}_noised_e1_step_{global_step}.safetensors"
                save_safetensors(adapter, path)

            pbar.set_postfix(loss=float(total_loss))

        final = output_dir / f"dual_shunt_omega_{t5_prompt_mode}_noised_e1_final.safetensors"
        save_safetensors(adapter, final)
        print(f"✅ Epoch {epoch} complete. Final model saved.")


In [ ]:
train_dual_shunt(
    t5_tok=t5_tok,
    clip_tok=clip_tok,
    t5_mod=t5_mod,
    clip_mod=clip_mod,
    adapter=adapter,
    repo_id="AbstractPhil/human-templated-captions-1b",
    batch_size=256,
    epochs=1,
    lr=1e-4,
    device="cuda",
    g_target=7.5,
    save_every=1000,
    seed=42,
    max_token_length=77,
    t5_prompt_mode="no_caption",
    output_dir="/content/drive/MyDrive/dual_shunt_runs_omega_g"
)


Epoch 1/1:   0%|          | 100/117187 [03:36<69:52:34,  2.15s/it, loss=1.4]

Gate mean: 0.270  log_sigma mean: -0.672


Epoch 1/1:   0%|          | 200/117187 [07:12<70:05:53,  2.16s/it, loss=1.38]

Gate mean: 0.270  log_sigma mean: -0.504


Epoch 1/1:   0%|          | 300/117187 [11:30<70:27:44,  2.17s/it, loss=1.37]

...

Epoch 1/1:   6%|▌         | 7000/117187 [4:13:11<68:46:49,  2.25s/it, loss=1.34]

✅ Model saved to /content/drive/MyDrive/dual_shunt_runs_omega_g/dual_shunt_omega_no_caption_noised_e1_step_7000.safetensors


Epoch 1/1:   6%|▌         | 7100/117187 [4:16:47<65:48:45,  2.15s/it, loss=1.34]

Gate mean: 0.270  log_sigma mean: -0.617


Epoch 1/1:   6%|▌         | 7159/117187 [4:18:55<65:55:30,  2.16s/it, loss=1.34]

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# summarization train

In [7]:
from pathlib import Path
from tqdm import tqdm
import torch
import torch.nn.functional as F
from torch.utils.data import DataLoader

def train_dual_shunt(
    t5_tok, clip_tok, t5_mod, clip_mod, adapter,
    repo_id: str,
    batch_size: int = 256,
    epochs: int = 1,
    lr: float = 5e-4,
    device: str = "cuda",
    g_target: float = 7.5,
    λ_delta: float = 1.0,
    λ_gate: float = 0.15,
    λ_ent: float = 0.02,
    λ_tau: float = 0.02,
    λ_anchor: float = 0.12,
    λ_guid: float = 0.1,
    save_every: int = 1000,
    max_token_length: int = 77,
    seed: int = 42,
    t5_prompt_mode: str = "summarization_curriculum",
    output_dir: str = "/content/drive/MyDrive/dual_shunt_runs_omega_g"
):
    def seed_everything(seed: int = 42):
        torch.manual_seed(seed)
        torch.cuda.manual_seed_all(seed)
        torch.backends.cudnn.deterministic = True
        torch.backends.cudnn.benchmark = False

    def hetero_loss(delta, target, log_sigma):
        LOG_2PI = 1.83787706641
        log_sigma = log_sigma.clamp(-5.0, 5.0)
        inv_var = torch.exp(-log_sigma)
        return 0.5 * (inv_var * (delta - target) ** 2 + log_sigma + LOG_2PI).mean()

    def entropy(p: torch.Tensor) -> torch.Tensor:
        p = p / (p.sum(-1, keepdim=True) + 1e-9)
        return -(p * (p + 1e-9).log()).sum(-1).mean()

    # Setup
    seed_everything(seed)
    device = torch.device(device)
    ds = ParsedMultiCharDataset(repo_id, start_file=50, num_files=6, shuffle=True)
    dl = DataLoader(ds, batch_size=batch_size, num_workers=4, drop_last=True,
                    persistent_workers=True, generator=torch.Generator().manual_seed(seed),
                    prefetch_factor=8)

    output_dir = Path(output_dir)
    output_dir.mkdir(parents=True, exist_ok=True)
    global_step = 0

    opt = torch.optim.AdamW(adapter.parameters(), lr=lr)
    scaler = torch.cuda.amp.GradScaler()

    for epoch in range(1, epochs + 1):
        pbar = tqdm(dl, desc=f"Epoch {epoch}/{epochs}")
        for texts in pbar:
            global_step += 1

            with torch.autocast(device.type, dtype=torch.bfloat16):
                # T5 encoding
                t5_inputs = t5_tok(texts, padding=True, truncation=True,
                                   max_length=max_token_length, return_tensors="pt").to(device)
                with torch.no_grad():
                    t5_seq = t5_mod(**t5_inputs).last_hidden_state

                # CLIP (plain)
                clip_inputs = clip_tok(texts, padding="max_length", truncation=True,
                                       max_length=max_token_length, return_tensors="pt").to(device)
                with torch.no_grad():
                    clip_seq_plain = clip_mod(**clip_inputs).last_hidden_state

                # Generate summaries
                with torch.no_grad():
                    summary_ids = t5_mod.generate(**t5_inputs, max_length=max_token_length)
                    cap_texts = t5_tok.batch_decode(summary_ids, skip_special_tokens=True)
                    clip_inputs_cap = clip_tok(cap_texts, padding="max_length", truncation=True,
                                               max_length=max_token_length, return_tensors="pt").to(device)
                    clip_seq_summary = clip_mod(**clip_inputs_cap).last_hidden_state

                    null_clip_inputs = clip_tok([""] * len(texts), padding="max_length", truncation=True,
                                                max_length=max_token_length, return_tensors="pt").to(device)
                    clip_seq_null = clip_mod(**null_clip_inputs).last_hidden_state

                # Curriculum interpolation
                interpolation = min(global_step / 10000.0, 1.0)
                clip_seq_cap = (1.0 - interpolation) * clip_seq_null + interpolation * clip_seq_summary
                delta_tgt = clip_seq_cap - clip_seq_plain

                # Adapter forward
                anchor, delta, log_sigma, attn_t2c, attn_c2t, tau, g_pred, gate = adapter(t5_seq, clip_seq_plain)

                with torch.no_grad():
                    t5_b = adapter.proj_t5(t5_seq)
                    clip_b = adapter.proj_clip(clip_seq_plain)
                    t2c_base, _ = adapter.cross_t2c(t5_b, clip_b, clip_b)
                    c2t_base, _ = adapter.cross_c2t(clip_b, t5_b, t5_b)

                pocket = adapter.pocket_blocks(t2c_base.detach())
                loss_pocket = F.mse_loss(pocket, t2c_base.detach()) * 0.05

                fused_h = adapter.fuse(torch.cat([
                    pocket.mean(1, keepdim=True).expand(-1, clip_b.size(1), -1),
                    c2t_base
                ], dim=-1))
                loss_hidden = (fused_h.norm(dim=-1).mean() - 1.0).abs() * 0.01

                # Losses
                warmup = min(global_step / 5000.0, 1.0)
                loss_delta = hetero_loss(delta, delta_tgt, log_sigma) * λ_delta * warmup

                gate_target_mean = 0.25 + 0.15 * interpolation
                loss_gate = (gate.mean() - gate_target_mean).abs() * λ_gate

                loss_ent = 0.5 * (entropy(attn_t2c) + entropy(attn_c2t)) * λ_ent
                loss_tau = tau.abs().mean() * λ_tau
                loss_anchor = (1 - F.cosine_similarity(anchor.mean(1), clip_seq_plain.mean(1), dim=-1).mean()) * λ_anchor
                loss_guid = F.mse_loss(g_pred, torch.full_like(g_pred, g_target)) * λ_guid

                total_loss = (
                    loss_delta + loss_gate + loss_ent +
                    loss_tau + loss_anchor + loss_guid +
                    loss_pocket + loss_hidden
                )

            # Backprop + step
            scaler.scale(total_loss).backward()
            scaler.step(opt)
            scaler.update()
            opt.zero_grad(set_to_none=True)

            if global_step % 100 == 0:
                print(f"[Step {global_step}] Loss: {total_loss.item():.4f}  Gate Mean: {gate.mean().item():.3f}")

            if global_step % save_every == 0:
                save_path = output_dir / f"dual_shunt_omega_{t5_prompt_mode}_e{epoch}_step_{global_step}.safetensors"
                save_safetensors(adapter, save_path)

        final = output_dir / f"dual_shunt_omega_{t5_prompt_mode}_e{epoch}_final.safetensors"
        save_safetensors(adapter, final)
        print(f"✅ Epoch {epoch} complete. Final model saved to {final}")


In [8]:
train_dual_shunt(
    t5_tok=t5_tok,
    clip_tok=clip_tok,
    t5_mod=t5_mod,
    clip_mod=clip_mod,
    adapter=adapter,
    repo_id="AbstractPhil/human-templated-captions-1b",
    batch_size=256,
    epochs=1,
    lr=1e-4,
    device="cuda",
    g_target=7.5,
    save_every=1000,
    seed=42,
    max_token_length=77,
    t5_prompt_mode="no_caption",
    output_dir="/content/drive/MyDrive/dual_shunt_runs_omega_g"
)


<ipython-input-7-50f64bd900da>:56: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = torch.cuda.amp.GradScaler()
Epoch 1/1:   0%|          | 0/117187 [00:01<?, ?it/s]


AttributeError: 'T5EncoderModel' object has no attribute 'generate'